In [1]:
from mesa import Model, Agent
from mesa.datacollection import DataCollector
from mesa.time import SimultaneousActivation


class SmallWorldAgentBasic(Agent):

    def __init__(self, unique_id, neighbors,  model):
        '''
         Create a new small world agent.

         Args:
            unique_id: Unique identifier for the agent
            neighbors: list of directly reachable agents
        '''

        super().__init__(unique_id, model)
        self.neighbors = neighbors

        self.infected = False
        self.newly_infected = False
        self.dead = False
        self.candidate_infections = []

    def step(self):
        '''
        Run one step of the agent.
        '''
        self.candidate_infections = []
        if self.dead:
            return

        if self.newly_infected:
            self.infected = True

        if self.infected:
            for neighbor in self.neighbors:
                if self.model.random.random() < self.model.infect_probability:
                    self.candidate_infections.append(neighbor)

    def advance(self):
        '''
        advance step of model
        '''

        if self.dead:
            return

        if self.infected:
            for candidate in self.candidate_infections:
                candidate.newly_infected = True
                print("Agent "+str(candidate.unique_id)+" got infected.\n")
            self.dead = True
            print("Agent "+str(self.unique_id)+" died.\n")


In [5]:
class SmallWorldModel(Model):

    def __init__(self, N, k, p, r):
        '''
        Create a new small world model.

         Args:
            N: how many agents the model contains
            k: how many neighbors an agent has CURRENTLY ONLY EVEN K SUPPORTED
            p: probability of rearranging edge in initialization
            r: probability of infecting another agent
        '''

        super().__init__()

        # 1 Initialization
        self.num_agents = N
        self.num_neighbors = k
        self.swap_probability = p
        self.infect_probability = r

        self.schedule = SimultaneousActivation(self)
        '''
        self.datacollector = DataCollector(  # < Note that we have both an agent and model data collector
            model_reporters={"Opinion_groups": get_number_opinion_groups}, agent_reporters={"Opinion": "opinion"}
        )
        '''
        # Create agents
        for i in range(self.num_agents):
            agent = SmallWorldAgentBasic(i, [0]*k, self)
            self.schedule.add(agent)

        agents = self.schedule.agents
        
        self.datacollector = DataCollector(
            agent_reporters={"Infected": "infected"}
        )

        # make the k nearest neighbors the official neighbors
        for j in range(int(self.num_neighbors / 2)):
            for i in range(self.num_agents):
                right = (i + j + 1) % self.num_agents
                left = (i - j - 1) % self.num_agents
                agents[i].neighbors[j*2] = agents[right]
                agents[i].neighbors[j*2+1] = agents[left]

        # randomly replace neighbors with new neighbors
        for j in range(self.num_neighbors):
            for i in range(self.num_agents):
                if self.random.random() < self.swap_probability:
                    candidate_agent = self.random.choice(self.schedule.agents)
                    already_connected = True
                    while already_connected:
                        in_neighbors = False
                        for neighbor in agents[i].neighbors:
                            if neighbor == candidate_agent:
                                in_neighbors = True
                        if in_neighbors:
                            candidate_agent = self.random.choice(self.schedule.agents)
                            already_connected = True
                        else:
                            already_connected = False
                    agents[i].neighbors[j] = candidate_agent
                    print("Agent "+str(i)+"'s new Neighbor on position "+str(j)+" is now Agent "+str(candidate_agent.unique_id)+".\n")

        # infect 1 agent
        patient_zero = self.random.choice(self.schedule.agents)
        patient_zero.infected = True
        print("Agent " + str(patient_zero.unique_id) + " got infected.\n")



    def step(self):
        '''
        Run one step of the model. If All agents are happy, halt the model.
        '''

        # 3 Step model function
        self.datacollector.collect(self)
        self.schedule.step()

In [22]:
model = SmallWorldModel(100, 4, 0.2, 0.5)
while model.schedule.steps < 100:
    model.step()

Agent 13's new Neighbor on position 0 is now Agent 39.

Agent 19's new Neighbor on position 0 is now Agent 31.

Agent 23's new Neighbor on position 0 is now Agent 96.

Agent 32's new Neighbor on position 0 is now Agent 87.

Agent 55's new Neighbor on position 0 is now Agent 13.

Agent 60's new Neighbor on position 0 is now Agent 21.

Agent 61's new Neighbor on position 0 is now Agent 10.

Agent 65's new Neighbor on position 0 is now Agent 17.

Agent 68's new Neighbor on position 0 is now Agent 41.

Agent 71's new Neighbor on position 0 is now Agent 40.

Agent 73's new Neighbor on position 0 is now Agent 79.

Agent 76's new Neighbor on position 0 is now Agent 1.

Agent 82's new Neighbor on position 0 is now Agent 51.

Agent 84's new Neighbor on position 0 is now Agent 17.

Agent 98's new Neighbor on position 0 is now Agent 4.

Agent 0's new Neighbor on position 1 is now Agent 10.

Agent 1's new Neighbor on position 1 is now Agent 63.

Agent 18's new Neighbor on position 1 is now Agent 9

In [23]:
params = {"N": 100, "k": 4, "p": 0.2, "r": 0.5}

In [25]:
from mesa.batchrunner import batch_run

results = batch_run(
    SmallWorldModel,
    parameters=params,
    iterations= 10,
    max_steps= 1,
    number_processes=1,
    data_collection_period= -1,
    display_progress=True,
)

275it [00:00, 1372.00it/s]

Agent 3's new Neighbor on position 0 is now Agent 38.

Agent 4's new Neighbor on position 0 is now Agent 21.

Agent 7's new Neighbor on position 0 is now Agent 21.

Agent 14's new Neighbor on position 0 is now Agent 81.

Agent 24's new Neighbor on position 0 is now Agent 99.

Agent 30's new Neighbor on position 0 is now Agent 94.

Agent 35's new Neighbor on position 0 is now Agent 57.

Agent 36's new Neighbor on position 0 is now Agent 79.

Agent 37's new Neighbor on position 0 is now Agent 20.

Agent 43's new Neighbor on position 0 is now Agent 33.

Agent 47's new Neighbor on position 0 is now Agent 93.

Agent 60's new Neighbor on position 0 is now Agent 11.

Agent 63's new Neighbor on position 0 is now Agent 73.

Agent 64's new Neighbor on position 0 is now Agent 24.

Agent 65's new Neighbor on position 0 is now Agent 50.

Agent 70's new Neighbor on position 0 is now Agent 41.

Agent 72's new Neighbor on position 0 is now Agent 44.

Agent 88's new Neighbor on position 0 is now Agent 

680it [00:00, 1297.76it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

1087it [00:00, 1327.34it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

1491it [00:01, 1235.01it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=

Agent 79 died.

Agent 2's new Neighbor on position 0 is now Agent 27.

Agent 4's new Neighbor on position 0 is now Agent 45.

Agent 5's new Neighbor on position 0 is now Agent 86.

Agent 6's new Neighbor on position 0 is now Agent 41.

Agent 9's new Neighbor on position 0 is now Agent 34.

Agent 11's new Neighbor on position 0 is now Agent 59.

Agent 12's new Neighbor on position 0 is now Agent 85.

Agent 20's new Neighbor on position 0 is now Agent 83.

Agent 31's new Neighbor on position 0 is now Agent 11.

Agent 40's new Neighbor on position 0 is now Agent 22.

Agent 43's new Neighbor on position 0 is now Agent 87.

Agent 51's new Neighbor on position 0 is now Agent 68.

Agent 58's new Neighbor on position 0 is now Agent 79.

Agent 59's new Neighbor on position 0 is now Agent 23.

Agent 61's new Neighbor on position 0 is now Agent 25.

Agent 62's new Neighbor on position 0 is now Agent 65.

Agent 63's new Neighbor on position 0 is now Agent 59.

Agent 64's new Neighbor on position 0

4814it [00:03, 1284.58it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

5218it [00:04, 1319.27it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)

5486it [00:04, 1310.40it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit

Agent 31 got infected.

Agent 33 died.

Agent 78 got infected.

Agent 53 got infected.

Agent 55 died.

Agent 54 got infected.

Agent 56 died.

Agent 61 got infected.

Agent 57 got infected.

Agent 59 died.

Agent 5's new Neighbor on position 0 is now Agent 22.

Agent 6's new Neighbor on position 0 is now Agent 89.

Agent 7's new Neighbor on position 0 is now Agent 46.

Agent 9's new Neighbor on position 0 is now Agent 81.

Agent 15's new Neighbor on position 0 is now Agent 22.

Agent 17's new Neighbor on position 0 is now Agent 65.

Agent 20's new Neighbor on position 0 is now Agent 50.

Agent 27's new Neighbor on position 0 is now Agent 14.

Agent 29's new Neighbor on position 0 is now Agent 4.

Agent 32's new Neighbor on position 0 is now Agent 13.

Agent 38's new Neighbor on position 0 is now Agent 28.

Agent 44's new Neighbor on position 0 is now Agent 48.

Agent 48's new Neighbor on position 0 is now Agent 94.

Agent 52's new Neighbor on position 0 is now Agent 8.

Agent 54's new

8419it [00:06, 1271.61it/s]

Agent 75's new Neighbor on position 1 is now Agent 27.

Agent 76's new Neighbor on position 1 is now Agent 5.

Agent 78's new Neighbor on position 1 is now Agent 5.

Agent 82's new Neighbor on position 1 is now Agent 65.

Agent 85's new Neighbor on position 1 is now Agent 62.

Agent 91's new Neighbor on position 1 is now Agent 70.

Agent 95's new Neighbor on position 1 is now Agent 10.

Agent 0's new Neighbor on position 2 is now Agent 58.

Agent 11's new Neighbor on position 2 is now Agent 31.

Agent 12's new Neighbor on position 2 is now Agent 42.

Agent 25's new Neighbor on position 2 is now Agent 15.

Agent 47's new Neighbor on position 2 is now Agent 99.

Agent 48's new Neighbor on position 2 is now Agent 19.

Agent 57's new Neighbor on position 2 is now Agent 36.

Agent 72's new Neighbor on position 2 is now Agent 32.

Agent 73's new Neighbor on position 2 is now Agent 83.

Agent 78's new Neighbor on position 2 is now Agent 47.

Agent 79's new Neighbor on position 2 is now Agent 

8814it [00:06, 1241.00it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [26]:
import pandas as pd

results_df = pd.DataFrame(results)
results_df.head()

RunId  iteration  Step    N  k    p    r  AgentID  Infected
0      0         -1     1  100  4  0.2  0.5        0     False
1      0         -1     1  100  4  0.2  0.5        1     False
2      0         -1     1  100  4  0.2  0.5        2     False
3      0         -1     1  100  4  0.2  0.5        3     False
4      0         -1     1  100  4  0.2  0.5        4     False